In [1]:
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\DELL\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [2]:
movies_data = pd.read_csv('final_data.csv')
movies_data1 = movies_data.copy()

In [3]:
movies_data1.drop(['url','PosterLink','DatePublished','RatingCount','BestRating','WorstRating','RatingValue','ReviewAurthor','ReviewBody','ReviewDate','duration'],inplace=True,axis=1)

In [4]:
movies_data1.isnull().sum()
movies_data2 = movies_data1.fillna('not found ')
movies_data2

id                                       Name  \
0          0                 Sallie Gardner at a Gallop   
1          1                            Buffalo Running   
2          2              Man Walking Around the Corner   
3          3              Traffic Crossing Leeds Bridge   
4          4                      Roundhay Garden Scene   
...      ...                                        ...   
48508  48508                                 The Batman   
48509  48509  Fantastic Beasts and Where to Find Them 3   
48510  48510                           Black Panther II   
48511  48511                                   Avatar 3   
48512  48512                                   Avatar 4   

                                         Genres  \
0                             Documentary,Short   
1                             Documentary,Short   
2                             Documentary,Short   
3                             Documentary,Short   
4                             Documentary,Short   
...                                         ...   
48508                        Action,Crime,Drama   
48509                  Adventure,Family,Fantasy   
48510    Action,Adventure,Drama,Sci-Fi,Thriller   
48511  Action,Adventure,Fantasy,Sci-Fi,Thriller   
48512  Action,Adventure,Fantasy,Sci-Fi,Thriller   

                                                  Actors  \
0                            Gilbert Domm,Sallie Gardner   
1                                             not found    
2                                             not found    
3                                           Cj Pallister   
4      Annie Hartley,Adolphe Le Prince,Joseph Whitley...   
...                                                  ...   
48508  Robert Pattinson,Colin Farrell,Andy Serkis,Zoë...   
48509   Mads Mikkelsen,Jude Law,Alison Sudol,Ezra Miller   
48510                                       Danai Gurira   
48511  Michelle Yeoh,Zoe Saldana,David Thewlis,Sam Wo...   
48512  Michelle Yeoh,Zoe Saldana,Sam Worthington,Sigo...   

                            Director  \
0                 Eadweard Muybridge   
1                 Eadweard Muybridge   
2      Louis Aimé Augustin Le Prince   
3      Louis Aimé Augustin Le Prince   
4      Louis Aimé Augustin Le Prince   
...                              ...   
48508                    Matt Reeves   
48509                    David Yates   
48510                   Ryan Coogler   
48511                  James Cameron   
48512                  James Cameron   

                                             Description  \
0      Sallie Gardner at a Gallop is a short starring...   
1                                             not found    
2                                             not found    
3      Traffic Crossing Leeds Bridge is a short starr...   
4      Roundhay Garden Scene is a short starring Anni...   
...                                                  ...   
48508  The Batman is a movie starring Robert Pattinso...   
48509  Fantastic Beasts and Where to Find Them 3 is a...   
48510  Black Panther II is a movie starring Danai Gur...   
48511  Avatar 3 is a movie starring Michelle Yeoh, Zo...   
48512  Avatar 4 is a movie starring Michelle Yeoh, Zo...   

                                                Keywords  
0           19th century,1870s,nature,horse,horse riding  
1      1880s,19th century,buffalo running,american bi...  
2                             walking,one man show,1880s  
3                 bridge,street life,1880s,traffic,horse  
4      place name in title,first of its kind,garden,1...  
...                                                  ...  
48508  superhero,based on comic,dc comics,batman char...  
48509  shared universe,rio de janeiro brazil,third pa...  
48510  sequel,second part,superhero,marvel comics,mar...  
48511  3d,number 3 in title,third part,sequel,number ...  
48512  3d,number 4 in title,fourth part,sequel,number...  

[48513 rows x 7 columns]

# Normalizing, StopWords Removal and Indexing

In [5]:
stop_words = set(stopwords.words('english'))

def Normalize_Words(key):
    
    lower_string = key.lower()
    no_number_string = re.sub(r'\d+','',lower_string)
    no_punc_string = re.sub(r'[^\w\s]','', no_number_string)
    no_wspace_string = no_punc_string.strip()
    
    if no_wspace_string == '':
        return None
    
    if no_wspace_string in stop_words:
        return None
    
    return no_wspace_string


class DocId:  
    def __init__(self, docId):
        self.docId = docId
        self.next = None
        

iwd = {}
stop_words = set(stopwords.words('english'))
movies_data3 = movies_data2.copy()

for i, des in enumerate(movies_data3['Description']):
    word_tokens = word_tokenize(des)
    for word_token in word_tokens:
        token = Normalize_Words(word_token)
        if token == None:
            continue
        else:
            word_token = token
            
        if word_token in iwd and iwd[word_token][1].docId < i:
            iwd[word_token][1].next = DocId(i)
            iwd[word_token][1] = iwd[word_token][1].next
        elif word_token not in iwd:
            node = DocId(i)
            iwd[word_token] = [node, node]

def print_inverted_index(iwd):
    for key in iwd:
        print(key,end=' ')
        cnode = iwd[key][0]
        while cnode != None:
            print(cnode.docId, end=' ')
            cnode = cnode.next
        
        print(' ')
        
# print_inverted_index(iwd)


# Searching

In [6]:
user_string = input('Give any description about a movie... we recommend movies for you...')
print(' ')
print(user_string)
print(' ')

user_tokens = word_tokenize(user_string)
user_tokens
final_user_tokens = []

for token in user_tokens:
    final_user_tokens.append(token.lower())

user_dict = {}
docId_list = []

def print_inverted(iwd):
    index = 0
    for key in iwd:
        print(key,end=' ')
        cnode = iwd[key][0]
        while cnode != None:
            print(cnode.docId, end=' ')
            docId_list.insert(index, cnode.docId)
            index += 1
            cnode = cnode.next
        
        print(' ')
        
        
for i,word in enumerate(final_user_tokens):
    if word in iwd:
        user_dict[word] = iwd[word]
        
print_inverted(user_dict)
print(' ')
docId_set = set(docId_list)
print(docId_set)
print(' ')

if len(docId_set) == 0:
    print('No movies based on your description...')
else:
    for item in docId_set:
        if item in movies_data3['id']:
            print(movies_data3.loc[item])
            print(' ')

Give any description about a movie... we recommend movies for you...eskfneks
 
eskfneks
 
 
set()
 
No movies based on your description...


# Indexing using Genres

In [7]:
stop_words = set(stopwords.words('english'))

def Normalize_Words(key):
    
    lower_string = key.lower()
    no_number_string = re.sub(r'\d+','',lower_string)
    no_punc_string = re.sub(r'[^\w\s]','', no_number_string)
    no_wspace_string = no_punc_string.strip()
    
    if no_wspace_string == '':
        return None
    
    if no_wspace_string in stop_words:
        return None
    
    return no_wspace_string


class DocId:  
    def __init__(self, docId):
        self.docId = docId
        self.next = None
        

iwd = {}
stop_words = set(stopwords.words('english'))
# movies_data3 = movies_data2.drop(movies_data2.index[3001:],inplace=False)

for i, des in enumerate(movies_data3['Genres']):
    word_tokens = word_tokenize(des)
    for word_token in word_tokens:
        token = Normalize_Words(word_token)
        if token == None:
            continue
        else:
            word_token = token
            
        if word_token in iwd and iwd[word_token][1].docId < i:
            iwd[word_token][1].next = DocId(i)
            iwd[word_token][1] = iwd[word_token][1].next
        elif word_token not in iwd:
            node = DocId(i)
            iwd[word_token] = [node, node]

def print_inverted_index(iwd):
    for key in iwd:
        print(key,end=' ')
        cnode = iwd[key][0]
        while cnode != None:
            print(cnode.docId, end=' ')
            cnode = cnode.next
        
        print(' ')
        
# print_inverted_index(iwd)


# Searching using Genres

In [8]:
user_string = input('Give any Genre of a movie... we recommend movies for you...')
print(' ')

user_tokens = word_tokenize(user_string)
user_tokens
final_user_tokens = []

for token in user_tokens:
    final_user_tokens.append(token.lower())

user_dict = {}
docId_list = []

def print_inverted(iwd):
    index = 0
    for key in iwd:
        print(key,end=' ')
        cnode = iwd[key][0]
        while cnode != None:
#             print(cnode.docId, end=' ')
            docId_list.insert(index, cnode.docId)
            index += 1
            cnode = cnode.next
        
        print(' ')
        
        
for i,word in enumerate(final_user_tokens):
    if word in iwd:
        user_dict[word] = iwd[word]
        
print_inverted(user_dict)
print(' ')
docId_set = set(docId_list)
# print('docId_set:','\n',  docId_set)
# print(' ')
print('docId_set is of length', len(docId_list))
print(' ')
print('Movies based on your search:')
print(' ')
count = 0
if len(docId_set) == 0:
    print('No movies based on your genre...')
else:
    for item in docId_set:
        if item in movies_data3['id']:
            print(movies_data3.loc[item])
            count += 1
            print(' ')
        
print('Total no.of movies:', count)

Give any Genre of a movie... we recommend movies for you...romance
 
romance  
 
docId_set is of length 9093
 
Movies based on your search:
 
id                                                         32768
Name                                                       Ricky
Genres                      Comedy,Drama,Fantasy,Mystery,Romance
Actors         Alexandra Lamy,Sergi López,Mélusine Mayance,Ar...
Director                                           François Ozon
Description    Ricky is a movie starring Alexandra Lamy, Serg...
Keywords       character name as title,baby,co worker,baby bo...
Name: 32768, dtype: object
 
id                                                         32775
Name                                               Up in the Air
Genres                                      Comedy,Drama,Romance
Actors         George Clooney,Vera Farmiga,Anna Kendrick,Jaso...
Director                                           Jason Reitman
Description    Up in the Air is a movie starring 

Name: 33153, dtype: object
 
id                                                         33157
Name                                       Before You Say 'I Do'
Genres                              Comedy,Drama,Fantasy,Romance
Actors         David Sutcliffe,Jennifer Westfeldt,Lauren Holl...
Director                                                Paul Fox
Description    Before You Say 'I Do' is a TV movie starring D...
Keywords               wedding,the past,wish,ten years,newspaper
Name: 33157, dtype: object
 
id                                                           391
Name                                               Way Down East
Genres                                             Drama,Romance
Actors         Lillian Gish,Richard Barthelmess,Mrs. David La...
Director                                           D.W. Griffith
Description    Way Down East is a movie starring Lillian Gish...
Keywords       blockbuster,fake wedding,country girl,female p...
Name: 391, dtype: object
 
id   

Name: 607, dtype: object
 
id                                                           611
Name                                         The Pleasure Garden
Genres                                             Drama,Romance
Actors         Virginia Valli,Carmelita Geraghty,Miles Mander...
Director                                        Alfred Hitchcock
Description    The Pleasure Garden is a movie starring Virgin...
Keywords       chorus girl,directorial debut,infidelity,honey...
Name: 611, dtype: object
 
id                                                           612
Name                                                    Don Juan
Genres                                         Adventure,Romance
Actors         Jane Winton,John Roche,Warner Oland,Estelle Ta...
Director                                           Alan Crosland
Description    Don Juan is a movie starring Jane Winton, John...
Keywords       character name as title,don juan character,ces...
Name: 612, dtype: object
 
id       

Name: 765, dtype: object
 
id                                                         33533
Name                                                 Liebe Mauer
Genres                                      Comedy,Drama,Romance
Actors         Felicitas Woll,Maxim Mehmet,Anna Fischer,Thoma...
Director                                              Peter Timm
Description    Liebe Mauer is a movie starring Felicitas Woll...
Keywords       first date,love at first sight,berlin germany,...
Name: 33533, dtype: object
 
id                                                           767
Name                                             New York Nights
Genres                                 Crime,Drama,Music,Romance
Actors         Norma Talmadge,Gilbert Roland,John Wray,Lilyan...
Director                                         Lewis Milestone
Description    New York Nights is a movie starring Norma Talm...
Keywords       jazz age,chorus girl,unfaithfulness,speakeasy,...
Name: 767, dtype: object
 
id     

Name: 994, dtype: object
 
id                                                         33763
Name                      Présentation ou Charlotte et son steak
Genres                                      Comedy,Short,Romance
Actors         Jean-Luc Godard,Stéphane Audran,Anna Karina,An...
Director                                             Éric Rohmer
Description    Présentation ou Charlotte et son steak is a sh...
Keywords              winter,apartment,food in title,snow,france
Name: 33763, dtype: object
 
id                                                           997
Name                                             Behind the Mask
Genres                              Crime,Horror,Mystery,Romance
Actors         Jack Holt,Constance Cummings,Boris Karloff,Cla...
Director                                     John Francis Dillon
Description    Behind the Mask is a movie starring Jack Holt,...
Keywords       bare chested male bondage,deception,psychotron...
Name: 997, dtype: object
 
id     

...

 
id                                                         29660
Name                                               War and Peace
Genres                                 Drama,History,Romance,War
Actors         Clémence Poésy,Alessio Boni,Alexander Beyer,Ma...
Director                                              not found 
Description    War and Peace is a TV mini-series starring Clé...
Keywords       french,napoleon bonaparte character,napoleonic...
Name: 29660, dtype: object
 
id                                                         29662
Name                                           The Hottest State
Genres                                       Drama,Music,Romance
Actors         Mark Webber,Catalina Sandino Moreno,Laura Linn...
Director                                             Ethan Hawke
Description    The Hottest State is a movie starring Mark Web...
Keywords       texas,actor,written and directed by cast membe...
Name: 29662, dtype: object
 
id                            

Name: 30222, dtype: object
 
id                                                         30238
Name                                                  Cheeni Kum
Genres                                      Comedy,Drama,Romance
Actors           Amitabh Bachchan,Tabu,Paresh Rawal,Zohra Sehgal
Director                                                R. Balki
Description    Cheeni Kum is a movie starring Amitabh Bachcha...
Keywords       child in danger,sports fan,cricket the sport,d...
Name: 30238, dtype: object
 
id                                                         30241
Name                                               Lyubov-Morkov
Genres                                    Comedy,Fantasy,Romance
Actors         Yuriy Kutsenko,Christina Orbakaite,Evgeniy Sty...
Director                                    Aleksandr Strizhenov
Description    Lyubov-Morkov is a movie starring Yuriy Kutsen...
Keywords                                                    love
Name: 30241, dtype: object
 
id 

id                                                         30985
Name                                                   Far North
Genres                              Crime,Drama,Romance,Thriller
Actors         Michelle Yeoh,Michelle Krusiec,Sean Bean,Gary ...
Director                                            Asif Kapadia
Description    Far North is a movie starring Michelle Yeoh, M...
Keywords       mother murders daughter,face mask made of huma...
Name: 30985, dtype: object
 
id                                                         30989
Name                                                 The Duchess
Genres                           Biography,Drama,History,Romance
Actors         Keira Knightley,Ralph Fiennes,Dominic Cooper,C...
Director                                               Saul Dibb
Description    The Duchess is a movie starring Keira Knightle...
Keywords               marriage,duchess,heir,infidelity,adultery
Name: 30989, dtype: object
 
id                              

Name: 31531, dtype: object
 
id                                                         31532
Name                                                    Affinity
Genres                                             Drama,Romance
Actors         Zoë Tapper,Anna Madeley,Domini Blythe,Amanda P...
Director                                              Tim Fywell
Description    Affinity is a movie starring Zoë Tapper, Anna ...
Keywords       prison,thames,con artist,based on novel,spirit...
Name: 31532, dtype: object
 
id                                                         31535
Name                                              Lost in Austen
Genres                              Drama,Fantasy,Romance,Sci-Fi
Actors         Jemima Rooper,Elliot Cowan,Hugh Bonneville,Flo...
Director                                              not found 
Description    Lost in Austen is a TV mini-series starring Je...
Keywords       19th century,2000s,london england,united kingd...
Name: 31535, dtype: object
 
id 

Name: 32321, dtype: object
 
id                                                         32330
Name                                                  Cairo Time
Genres                                             Drama,Romance
Actors         Patricia Clarkson,Alexander Siddig,Elena Anaya...
Director                                              Ruba Nadda
Description    Cairo Time is a movie starring Patricia Clarks...
Keywords       title directed by female,title written by fema...
Name: 32330, dtype: object
 
id                                                         32333
Name                                                Love Happens
Genres                                             Drama,Romance
Actors         Jennifer Aniston,Aaron Eckhart,Dan Fogler,John...
Director                                            Brandon Camp
Description    Love Happens is a movie starring Jennifer Anis...
Keywords       florist,self help guru,widower,motivational sp...
Name: 32333, dtype: object
 
id 

# Indexing using Directors

In [9]:
movies_data4 = movies_data3.copy()
# movies_data4.insert(loc=8,
#           column='feedback',
#           value=input('Enter 1 or 0: '))

stop_words = set(stopwords.words('english'))

def Normalize_Words(key):
    
    lower_string = key.lower()
    no_number_string = re.sub(r'\d+','',lower_string)
    no_punc_string = re.sub(r'[^\w\s]','', no_number_string)
    no_wspace_string = no_punc_string.strip()
    
    if no_wspace_string == '':
        return None
    
    if no_wspace_string in stop_words:
        return None
    
    return no_wspace_string


class DocId:  
    def __init__(self, docId):
        self.docId = docId
        self.next = None
        

iwd = {}
stop_words = set(stopwords.words('english'))
# movies_data3 = movies_data2.drop(movies_data2.index[3001:],inplace=False)

for i, des in enumerate(movies_data3['Director']):
    word_tokens = word_tokenize(des)
    for word_token in word_tokens:
        token = Normalize_Words(word_token)
        if token == None:
            continue
        else:
            word_token = token
            
        if word_token in iwd and iwd[word_token][1].docId < i:
            iwd[word_token][1].next = DocId(i)
            iwd[word_token][1] = iwd[word_token][1].next
        elif word_token not in iwd:
            node = DocId(i)
            iwd[word_token] = [node, node]

def print_inverted_index(iwd):
    for key in iwd:
        print(key,end=' ')
        cnode = iwd[key][0]
        while cnode != None:
            print(cnode.docId, end=' ')
            cnode = cnode.next
        
        print(' ')
        
# print_inverted_index(iwd)


# Searching using directors names

In [11]:
user_string = input('Give any Director of a movie... we recommend movies for you...')
print(' ')

user_tokens = word_tokenize(user_string)
user_tokens
final_user_tokens = []

for token in user_tokens:
    final_user_tokens.append(token.lower())

user_dict = {}
docId_list = []

def print_inverted(iwd):
    index = 0
    for key in iwd:
        print(key,end=' ')
        cnode = iwd[key][0]
        while cnode != None:
#             print(cnode.docId, end=' ')
            docId_list.insert(index, cnode.docId)
            index += 1
            cnode = cnode.next
        
        print(' ')
        
        
for i,word in enumerate(final_user_tokens):
    if word in iwd:
        user_dict[word] = iwd[word]
        
print_inverted(user_dict)
print(' ')
docId_set = set(docId_list)
# print('docId_set:','\n',  docId_set)
# print(' ')
print('docId_set is of length', len(docId_list))
print(' ')
print('Movies based on your search:')
print(' ')
count = 0
retrieved_movies = []
if len(docId_set) == 0:
    print('No movies based on your given Director...')
else:
    for item in docId_set:
        if item in movies_data3['id']:
            print(movies_data3.loc[item])
            retrieved_movies.insert(count,movies_data3.loc[item])
            count += 1
            print(' ')
        
print('Total no.of movies:', count)

Give any Director of a movie... we recommend movies for you...james cameron
 
james  
cameron  
 
docId_set is of length 594
 
Movies based on your search:
 
id                                                         45057
Name                                                Little Birds
Genres                                                     Drama
Actors         Juno Temple,Kay Panabaker,Leslie Mann,Kate Bos...
Director                                             Elgin James
Description    Little Birds is a movie starring Juno Temple, ...
Keywords       attempted rape,sex scene,female nudity,bare br...
Name: 45057, dtype: object
 
id                                                         16394
Name                                             Heart Condition
Genres                                Comedy,Crime,Drama,Fantasy
Actors         Bob Hoskins,Denzel Washington,Chloe Webb,Roger...
Director                                       James D. Parriott
Description    Heart Condition is

id                                                         24835
Name                                         Ghosts of the Abyss
Genres                                        Documentary,Family
Actors         Bill Paxton,Lori Johnston,Lewis Abernathy,John...
Director                                           James Cameron
Description    Ghosts of the Abyss is a movie starring Bill P...
Keywords       underwater scene,titanic,shipwreck,expedition,...
Name: 24835, dtype: object
 
id                                                         39172
Name                                    The Jeffrey Dahmer Files
Genres                 Documentary,Biography,Crime,Drama,Mystery
Actors         Andrew Swant,Pamela Bass,Jeffrey Jentzen,Pat K...
Director                                    Chris James Thompson
Description    The Jeffrey Dahmer Files is a movie starring A...
Keywords       reenactment,serial killer,archival footage,pol...
Name: 39172, dtype: object
 
id                              

Name: 45588, dtype: object
 
id                                                         35350
Name                              The Fall of the House of Usher
Genres                                              Short,Horror
Actors         Herbert Stern,Hildegarde Watson,Melville Webbe...
Director                     James Sibley Watson,Melville Webber
Description    The Fall of the House of Usher is a short star...
Keywords       gothic horror,double exposure effects,sledgeha...
Name: 35350, dtype: object
 
id                                                         10777
Name                                                The Enforcer
Genres                                     Action,Crime,Thriller
Actors         Clint Eastwood,Tyne Daly,Harry Guardino,Bradfo...
Director                                             James Fargo
Description    The Enforcer is a movie starring Clint Eastwoo...
Keywords       ford torino,dirty harry,female nudity,male nud...
Name: 10777, dtype: object
 
id 

Name: 37632, dtype: object
 
id                                                         47872
Name                                Abacus: Small Enough to Jail
Genres                                               Documentary
Actors         Thomas Sung,Hwei Lin Sung,Cyrus Vance Jr.,Matt...
Director                                             Steve James
Description    Abacus: Small Enough to Jail is a movie starri...
Keywords               trial,prosecution,chinese,money,economics
Name: 47872, dtype: object
 
id                                                         31501
Name                                                  Two Lovers
Genres                                             Drama,Romance
Actors         Joaquin Phoenix,Gwyneth Paltrow,Vinessa Shaw,A...
Director                                              James Gray
Description    Two Lovers is a movie starring Joaquin Phoenix...
Keywords       cell phone,neighbor,photograph,married man,jewish
Name: 31501, dtype: object
 
id 

Name: 13349, dtype: object
 
id                                                         29735
Name                                                   Hellphone
Genres                                            Comedy,Fantasy
Actors         Jean-Baptiste Maunier,Jennifer Decker,Benjamin...
Director                                              James Huth
Description    Hellphone is a movie starring Jean-Baptiste Ma...
Keywords       teacher student relationship,supernatural powe...
Name: 29735, dtype: object
 
id                                                          3112
Name                                           Never Say Goodbye
Genres                                                    Comedy
Actors         Errol Flynn,Eleanor Parker,Lucile Watson,S.Z. ...
Director                                           James V. Kern
Description    Never Say Goodbye is a movie starring Errol Fl...
Keywords       screwball comedy,glamour models,model,referenc...
Name: 3112, dtype: object
 
id  

 
id                                                         30053
Name                                                Blue Harvest
Genres                                          Animation,Comedy
Actors         Seth MacFarlane,Alex Borstein,Seth Green,Mila ...
Director                 Dominic Polcino,James Purdum,Peter Shin
Description    Blue Harvest is an episode of Family Guy starr...
Keywords       reference to airplane,reference to princess le...
Name: 30053, dtype: object
 
id                                                         13679
Name                             Bloodbath at the House of Death
Genres                                             Horror,Comedy
Actors         Kenny Everett,Vincent Price,Pamela Stephenson,...
Director                                             Ray Cameron
Description    Bloodbath at the House of Death is a movie sta...
Keywords       bad guys win,tragic ending,characters killed o...
Name: 13679, dtype: object
 
id                            

 
id                                                         40628
Name                                      WNUF Halloween Special
Genres                                             Comedy,Horror
Actors         Paul Fahrenkopf,Aaron Henkin,Nicolette le Faye...
Director       Chris LaMartina,James Branscome,Shawn Jones,Sc...
Description    WNUF Halloween Special is a movie starring Pau...
Keywords       halloween,retro,retro horror,halloween costume...
Name: 40628, dtype: object
 
id                                                         46773
Name                                  I'll Be Home for Christmas
Genres                                      Drama,Family,Romance
Actors         James Brolin,Mena Suvari,Giselle Eisenberg,Joh...
Director                                            James Brolin
Description    I'll Be Home for Christmas is a TV movie starr...
Keywords       father daughter relationship,christmas tree,ge...
Name: 46773, dtype: object
 
id                            

Name: 36816, dtype: object
 
id                                                          2013
Name                                    Bulldog Drummond's Bride
Genres             Action,Adventure,Comedy,Crime,Mystery,Romance
Actors         John Howard,Heather Angel,H.B. Warner,Reginald...
Director                                          James P. Hogan
Description    Bulldog Drummond's Bride is a movie starring J...
Keywords       united kingdom,radio,apartment,bulldog drummon...
Name: 2013, dtype: object
 
id                                                          2014
Name                            Bulldog Drummond's Secret Police
Genres                                          Mystery,Thriller
Actors         John Howard,Heather Angel,H.B. Warner,Reginald...
Director                                          James P. Hogan
Description    Bulldog Drummond's Secret Police is a movie st...
Keywords       1930s,string of pearls,gold coin,sergeant,cons...
Name: 2014, dtype: object
 
id   

# Relevance Feedback

In [12]:
all_doc_id = []

for i,item in enumerate(retrieved_movies):
    print(item['id'], ' ', item['Director'])
    all_doc_id.insert(i,item['id'])
    
user_feedback_input = input('Enter feedback for the documents: ')

user_feedback_tokens = word_tokenize(user_feedback_input)
print(user_feedback_tokens)

45057   Elgin James
16394   James D. Parriott
2066   James Whale
26654   James Benning
24614   Steve Barron,Samuel Bayer,David Bowie,Rudi Dolezal,Stanley Dorfman,Nick Goffey,Dominic Hawley,David Mallet,Roger Michell,Jean-Baptiste Mondino,D.A. Pennebaker,Tim Pope,Mick Rock,Matthew Rolston,Mark Romanek,Hannes Rossacher,Floria Sigismondi,Walter A. Stern,Julien Temple,Gus Van Sant,James Yukich
36903   Cameron Casey
10289   David Greene,James Hill
30769   James Moll
38963   Elizabeth Banks,Steven Brill,Steve Carr,Rusty Cundieff,James Duffy,Griffin Dunne,Peter Farrelly,Patrik Forsberg,Will Graham,James Gunn,Brett Ratner,Jonathan van Tulleken,Bob Odenkirk
26676   James Benning
56   James H. White
57   James H. White
58   James H. White
47163   James Mangold
64   James H. White
24641   Beth McCarthy-Miller,Stacey Foster,James Signorelli
68   James H. White
28743   James Dodson
74   James H. White
38989   James Mangold
16466   James Ivory
16467   James Orr
38997   James Wan
41046   Jason James


7905   James Goldstone
5858   James Algar
44774   Devin Chanda,Matt Mitchenor,James Rothman
18160   James Dodson
14068   James Orr
1793   Alan James,William Witney
12033   James F. Collier
3853   James V. Kern
22291   James Wong
28437   James M. Hausler
42775   James Yukich
1826   James W. Horne
24355   James Keach
38693   Emma De Swaef,Marc James Roels
36646   James Hayman
1833   James Cruze
14121   James Frawley
42798   James Benning
22319   James Ivory
20272   James L. Brooks
30513   Brit McAdams,James Yukich
32565   James Wong
24385   James Hanlon,Gédéon Naudet,Jules Naudet
36674   James Moll
22339   James Head
44868   James Head
36675   Cameron Crowe
40775   James Lapine,Autumn de Wilde,Todd Haynes
34633   Steve James
1866   Mitchell Leisen,James P. Hogan
8011   James Neilson
20303   Steve James
24407   James Benning
1880   James P. Hogan
8032   James Goldstone
18273   Ben Burtt,Phyllis Ferguson,James Neihouse,Gail Singer
40823   James Benning
20345   James Frawley
22393   James M

In [13]:
dictionary = {}
dictionary[user_string] = user_feedback_tokens

In [14]:
user_query = input('Give any Director of a movie... we recommend movies for you...')
isThere = False

if user_query in dictionary:
    isThere = True
    for doc_id in dictionary[user_query]:
        if doc_id in all_doc_id:
            all_doc_id.remove(doc_id)
            
else:
    user_tokens = word_tokenize(user_query)
    user_tokens
    final_user_tokens = []

    for token in user_tokens:
        final_user_tokens.append(token.lower())

    user_dict = {}
    docId_list = []

    def print_inverted(iwd):
        index = 0
        for key in iwd:
            print(key,end=' ')
            cnode = iwd[key][0]
            while cnode != None:
    #             print(cnode.docId, end=' ')
                docId_list.insert(index, cnode.docId)
                index += 1
                cnode = cnode.next

            print(' ')


    for i,word in enumerate(final_user_tokens):
        if word in iwd:
            user_dict[word] = iwd[word]

    print_inverted(user_dict)
    print(' ')
    docId_set = set(docId_list)
    # print('docId_set:','\n',  docId_set)
    # print(' ')
    print('docId_set is of length', len(docId_list))
    print(' ')
    print('Movies based on your search:')
    print(' ')
    count = 0
    retrieved_movies = []
    if len(docId_set) == 0:
        print('No movies based on your given Director...')
    else:
        for item in docId_set:
            if item in movies_data3['id']:
                print(movies_data3.loc[item])
                retrieved_movies.insert(count,movies_data3.loc[item])
                count += 1
                print(' ')

    print('Total no.of movies:', count)
    
    
if isThere:
    for item in dictionary[user_query]:
        print(movies_data3.iloc[int(item)])
        
    for item in all_doc_id:
        print(movies_data3.iloc[int(item)])

Give any Director of a movie... we recommend movies for you...james cameron
id                                                         20378
Name                                                     Titanic
Genres                                             Drama,Romance
Actors         Leonardo DiCaprio,Kate Winslet,Billy Zane,Kath...
Director                                           James Cameron
Description    Titanic is a movie starring Leonardo DiCaprio,...
Keywords           iceberg,sailor's death,mass death,titanic,wet
Name: 20378, dtype: object
id                                                         48512
Name                                                    Avatar 4
Genres                  Action,Adventure,Fantasy,Sci-Fi,Thriller
Actors         Michelle Yeoh,Zoe Saldana,Sam Worthington,Sigo...
Director                                           James Cameron
Description    Avatar 4 is a movie starring Michelle Yeoh, Zo...
Keywords       3d,number 4 in title,fourth part,sequ

Name: 9214, dtype: object
id                                                          3076
Name                                            Deadline at Dawn
Genres                        Film-Noir,Mystery,Romance,Thriller
Actors         Susan Hayward,Paul Lukas,Bill Williams,Joseph ...
Director                  Harold Clurman,William Cameron Menzies
Description    Deadline at Dawn is a movie starring Susan Hay...
Keywords       naivety,no abnormal brother sister relationshi...
Name: 3076, dtype: object
id                                                         15365
Name                                     Bright Lights, Big City
Genres                                                     Drama
Actors         Michael J. Fox,Kiefer Sutherland,Phoebe Cates,...
Director                                           James Bridges
Description    Bright Lights, Big City is a movie starring Mi...
Keywords         writer,new york city,nightclub,magazine,cocaine
Name: 15365, dtype: object
id         

Name: 3853, dtype: object
id                                                         22291
Name                                           Final Destination
Genres                                           Horror,Thriller
Actors            Devon Sawa,Ali Larter,Kerr Smith,Kristen Cloke
Director                                              James Wong
Description    Final Destination is a movie starring Devon Sa...
Keywords       extrasensory perception,teen horror,teenage gi...
Name: 22291, dtype: object
id                                                         28437
Name                                                  Wild Seven
Genres                                               Crime,Drama
Actors         Richard Roundtree,Robert Loggia,Robert Forster...
Director                                        James M. Hausler
Description    Wild Seven is a movie starring Richard Roundtr...
Keywords                                              not found 
Name: 28437, dtype: object
id        

# Reading telugu dataset

In [40]:
telugu_movies = pd.read_csv('output.csv')
telugu_movies1 = telugu_movies.copy()
telugu_movies1['id'] = telugu_movies1.index
telugu_movies1

Name                            Genres  \
0                            కాడవర్             క్రైమ్ డ్రామా మిస్టరీ   
1                     ఆ పోరాటయోధుడు             యాక్షన్ క్రైమ్ డ్రామా   
2                          రంగస్థలం                    యాక్షన్ డ్రామా   
3                       రాధే శ్యామ్                           నాటకీయత   
4                             ఆడండి                  క్రిమి త్రిల్లర్   
5                         పునరావృతం                  క్రిమి త్రిల్లర్   
6                               ఈగా             యాక్షన్ కామెడీ డ్రామా   
7                            గాడ్సే                 యాక్షన్ థ్రిల్లర్   
8         పుష్ప: ది రూల్ - పార్ట్ 2             యాక్షన్ క్రైమ్ డ్రామా   
9                ఇంగ్లీష్ వింగ్లిష్             కామెడీ డ్రామా కుటుంబం   
10                        మన్నిన్చవ                           నాటకీయత   
11                          GAALODU                            డ్రామా   
12                           మగధీరా             యాక్షన్ డ్రామా ఫాంటసీ   
13                       365 రోజులు                           నాటకీయత   
14                అలా వైకుంతపురములూ             యాక్షన్ కామెడీ డ్రామా   
15                           జెట్టి           యాక్షన్ డ్రామా ఫ్యామిలీ   
16                           గిన్నా             యాక్షన్ కామెడీ డ్రామా   
17     ఇట్లు మారీడుమిల్లి ప్రజయకేమ్                            డ్రామా   
18                       డ్రూష్యం 2                  డ్రామా థ్రిల్లర్   
19                    ఓహ్ నా దెయ్యం                      కామెడీ హోరర్   
20                            అమ్మూ                            డ్రామా   
21                             కనమ్   డ్రామా సైన్స్ ఫిక్షన్ థ్రిల్లర్   
22                      అంతిమ ఘట్టం          యాక్షన్ హర్రర్ థ్రిల్లర్   
23                         DJ TULLU             యాక్షన్ కామెడీ క్రైమ్   
24               బాహుబలి 2: ముగింపు                    యాక్షన్ డ్రామా   
25                            మసూడా                    హర్రోర్రిల్లర్   
26                           దెయ్యం                 యాక్షన్ థ్రిల్లర్   
27                    ప్రమాదకరమైనది        యాక్షన్ రొమాన్స్ థ్రిల్లర్   
28                     నిథం ఓరు వనం                            డ్రామా   
29                        బింబిసారా             యాక్షన్ డ్రామా ఫాంటసీ   
30                         ప్రిన్స్            యాక్షన్ డ్రామ రోమెన్స్   
31              గంగూబాయ్ కాథియావాడి            బయోగ్రఫీ క్రిమె డ్రామా   
32        పుష్ప: ది రైజ్ - పార్ట్ 1             యాక్షన్ క్రైమ్ డ్రామా   
33                          జై భీమ్             క్రైమ్ డ్రామా మిస్టరీ   
34                            లిగర్            యాక్షన్ డ్రామ రోమెన్స్   
35                      కార్తికేయ 2          యాక్షన్ అడ్వెంచర్ ఫాంటసీ   
36                          విక్రమ్          యాక్షన్ క్రైమ్ థ్రిల్లర్   
37                           ప్రధాన           యాక్షన్ బయోగ్రఫీ డ్రామా   
38             నీలం రంగులో పురుషులు                  డ్రామా థ్రిల్లర్   
39                 బాహుబలి ప్రారంభం                    యాక్షన్ డ్రామా   
40                          కొట్టుట             యాక్షన్ క్రైమ్ డ్రామా   
41                             తపనా                          రొమాన్స్   
42              2 వ కేసును నొక్కండి             యాక్షన్ క్రైమ్ డ్రామా   
43                   ది జంగిల్ బుక్          అడ్వెంచర్ డ్రామా కుటుంబం   
44  బ్రహ్మాస్ట్రా పార్ట్ వన్ శివుడు          యాక్షన్ అడ్వెంచర్ ఫాంటసీ   
45                            యషోడా  యాక్షన్ సైన్స్ ఫిక్షన్ థ్రిల్లర్   
46                       గాడ్ ఫాదర్             యాక్షన్ క్రైమ్ డ్రామా   
47                              Rrr                    యాక్షన్ డ్రామా   
48                        సీత రామమ్            యాక్షన్ డ్రామా మిస్టరీ   

                  Actors                  Directors  \
0              అమలా పాల్              అనూప్ పానికర్   
1          రామ్ పోతినేని            ఎన్. లింగస్వామి   
2         రామ్ చరణ్ తేజా                   సుకుమార్   
3                ప్రభాస్                     కె.కె.   
4     అభినవ్ సింగ్ రాఘవ్                  మోక్స్ష్.   
5            నవీన్ చంద్ర        అరవింధ్ శ్రీనివాసన

# Indexing using genres

In [45]:
class DocId:  
    def __init__(self, docId):
        self.docId = docId
        self.next = None
        

iwd = {}

for i, des in enumerate(telugu_movies1['Genres']):
    word_tokens = word_tokenize(des)
    for word_token in word_tokens:
        if word_token in iwd and iwd[word_token][1].docId < i:
            iwd[word_token][1].next = DocId(i)
            iwd[word_token][1] = iwd[word_token][1].next
        elif word_token not in iwd:
            node = DocId(i)
            iwd[word_token] = [node, node]

def print_inverted_index(iwd):
    for key in iwd:
        print(key,end=' ')
        cnode = iwd[key][0]
        while cnode != None:
            print(cnode.docId, end=' ')
            cnode = cnode.next
        
        print(' ')
        
print_inverted_index(iwd)


క్రైమ్ 0 1 8 23 32 33 36 40 42 46  
డ్రామా 0 1 2 6 8 9 11 12 14 15 16 17 18 20 21 24 28 29 31 32 33 37 38 39 40 42 43 46 47 48  
మిస్టరీ 0 33 48  
యాక్షన్ 1 2 6 7 8 12 14 15 16 22 23 24 26 27 29 30 32 34 35 36 37 39 40 42 44 45 46 47 48  
నాటకీయత 3 10 13  
క్రిమి 4 5  
త్రిల్లర్ 4 5  
కామెడీ 6 9 14 16 19 23  
థ్రిల్లర్ 7 18 21 22 26 27 36 38 45  
కుటుంబం 9 43  
ఫాంటసీ 12 29 35 44  
ఫ్యామిలీ 15  
హోరర్ 19  
సైన్స్ 21 45  
ఫిక్షన్ 21 45  
హర్రర్ 22  
హర్రోర్రిల్లర్ 25  
రొమాన్స్ 27 41  
డ్రామ 30 34  
రోమెన్స్ 30 34  
బయోగ్రఫీ 31 37  
క్రిమె 31  
అడ్వెంచర్ 35 43 44  


# Searching using genres

In [46]:
user_string = input('Give any Genre of a movie... we recommend movies for you...')
print(' ')

user_tokens = word_tokenize(user_string)
user_tokens
final_user_tokens = []

for token in user_tokens:
    final_user_tokens.append(token.lower())

user_dict = {}
docId_list = []

def print_inverted(iwd):
    index = 0
    for key in iwd:
        print(key,end=' ')
        cnode = iwd[key][0]
        while cnode != None:
#             print(cnode.docId, end=' ')
            docId_list.insert(index, cnode.docId)
            index += 1
            cnode = cnode.next
        
        print(' ')
        
        
for i,word in enumerate(final_user_tokens):
    if word in iwd:
        user_dict[word] = iwd[word]
        
print_inverted(user_dict)
print(' ')
docId_set = set(docId_list)
# print('docId_set:','\n',  docId_set)
# print(' ')
print('docId_set is of length', len(docId_list))
print(' ')
print('Movies based on your search:')
print(' ')
count = 0
if len(docId_set) == 0:
    print('No movies based on your genre...')
else:
    for item in docId_set:
        if item in telugu_movies1['id']:
            print(telugu_movies1.loc[item])
            count += 1
            print(' ')
        
print('Total no.of movies:', count)

Give any Genre of a movie... we recommend movies for you...రొమాన్స్
 
రొమాన్స్  
 
docId_set is of length 2
 
Movies based on your search:
 
Name                                                        తపనా
Genres                                                  రొమాన్స్
Actors                                             ధారాన్ నాయుడు
Directors                                           కె. వెంకటేష్
Description    కె. వెంకటేష్ దర్శకత్వం వహించిన భారతీయ తెలుగు చ...
Keywords                                                     8.3
id                                                            41
Name: 41, dtype: object
 
Name                                               ప్రమాదకరమైనది
Genres                                యాక్షన్ రొమాన్స్ థ్రిల్లర్
Actors                                               నైనా గంగూలీ
Directors                                       రామ్ గోపాల్ వర్మ
Description    ప్రమాదకరమైనది ఇద్దరు మహిళల కథ వారు పురుషులతో క...
Keywords                                             

# Indexing using Actors

In [47]:
class DocId:  
    def __init__(self, docId):
        self.docId = docId
        self.next = None
        

iwd = {}

for i, des in enumerate(telugu_movies1['Actors']):
    word_tokens = word_tokenize(des)
    for word_token in word_tokens:
        if word_token in iwd and iwd[word_token][1].docId < i:
            iwd[word_token][1].next = DocId(i)
            iwd[word_token][1] = iwd[word_token][1].next
        elif word_token not in iwd:
            node = DocId(i)
            iwd[word_token] = [node, node]

def print_inverted_index(iwd):
    for key in iwd:
        print(key,end=' ')
        cnode = iwd[key][0]
        while cnode != None:
            print(cnode.docId, end=' ')
            cnode = cnode.next
        
        print(' ')
        
print_inverted_index(iwd)


అమలా 0  
పాల్ 0  
రామ్ 1 2 12 29  
పోతినేని 1  
చరణ్ 2 12  
తేజా 2 12  
ప్రభాస్ 3 24 39  
అభినవ్ 4  
సింగ్ 4  
రాఘవ్ 4  
నవీన్ 5  
చంద్ర 5  
సుదీప్ 6  
సత్యదేవ్ 7  
కాంచరణ 7  
రష్మికా 8  
మాండన్న 8  
శ్రీదేవి 9  
ఎస్ 10  
మల్హోత్రా 10  
శివుడు 10  
సాపగిరి 11  
రవి 13  
కొండాలా 13  
రావు 13  
అల్లు 14 32  
అర్జున్ 14 32  
నందిత 15  
శ్వేతా 15  
విష్ణు 16  
మంచు 16  
ఆనందీ 17  
వెంకటేష్ 18  
దబ్బీబాటి 18  
సన్నీ 19  
లియోన్ 19  
ఐశ్వర్య 20  
లెక్ష్మి 20  
సతిష్ 21  
శూన్య 22  
నేహా 23  
శెట్టి 23  
తిరువీర్ 25  
నాగార్జున 26  
అక్కినేని 26  
నైనా 27  
గంగూలీ 27  
అభిరామి 28  
నందమురి 29  
కళ్యాణ్ 29  
ప్రీంగి 30  
అమరెన్ 30  
అలియా 31  
భట్ 31  
సూరియా 33  
మైక్ 34  
టైసన్ 34  
నిఖిల్ 35  
సిద్ధార్థ్ 35  
కమల్ 36  
హాసన్ 36  
ఆదివి 37 42  
శేష్ 37 42  
కీకీ 38  
సుకి 38  
విశ్వక్ 40  
సేన్ 40  
ధారాన్ 41  
నాయుడు 41  
నీల్ 43  
సేథి 43  
అమితాబ్ 44  
బచ్చన్ 44  
సమంతా 45  
రూత్ 45  
ప్రభు 45  
చిరంజీవి 46  
N.T 47  
. 47  
దుల్క్వర్ 48  
సల్మాన్ 48  


# Searching using Actors

In [62]:
user_string = input('Give any Genre of a movie... we recommend movies for you...')
print(' ')
retrieved_movies = []

user_tokens = word_tokenize(user_string)
user_tokens
final_user_tokens = []

for token in user_tokens:
    final_user_tokens.append(token.lower())

user_dict = {}
docId_list = []

def print_inverted(iwd):
    index = 0
    for key in iwd:
        print(key,end=' ')
        cnode = iwd[key][0]
        while cnode != None:
#             print(cnode.docId, end=' ')
            docId_list.insert(index, cnode.docId)
            index += 1
            cnode = cnode.next
        
        print(' ')
        
        
for i,word in enumerate(final_user_tokens):
    if word in iwd:
        user_dict[word] = iwd[word]
        
print_inverted(user_dict)
print(' ')
docId_set = set(docId_list)
# print('docId_set:','\n',  docId_set)
# print(' ')
print('docId_set is of length', len(docId_list))
print(' ')
print('Movies based on your search:')
print(' ')
count = 0
if len(docId_set) == 0:
    print('No movies based on your genre...')
else:
    for item in docId_set:
        if item in telugu_movies1['id']:
            print(telugu_movies1.loc[item])
            retrieved_movies.insert(count,telugu_movies1.loc[item])
            count += 1
            print(' ')
        
print('Total no.of movies:', count)

Give any Genre of a movie... we recommend movies for you...రామ్ చరణ్ తేజా
 
రామ్  
చరణ్  
తేజా  
 
docId_set is of length 8
 
Movies based on your search:
 
Name                                               ఆ పోరాటయోధుడు
Genres                                     యాక్షన్ క్రైమ్ డ్రామా
Actors                                             రామ్ పోతినేని
Directors                                        ఎన్. లింగస్వామి
Description    సత్య గురువుకు వ్యతిరేకంగా తన గొంతును లేవనెత్తి...
Keywords                                                     4.7
id                                                             1
Name: 1, dtype: object
 
Name                                                    రంగస్థలం
Genres                                            యాక్షన్ డ్రామా
Actors                                            రామ్ చరణ్ తేజా
Directors                                               సుకుమార్
Description    చిట్టి బాబు తన అన్నయ్య జీవితానికి వారి గ్రామ అ...
Keywords                              

# Relevance Feedback

In [63]:
all_doc_id = []

for i,item in enumerate(retrieved_movies):
    print(item['id'], ' ', item['Actors'])
    all_doc_id.insert(i,item['id'])
    
user_feedback_input = input('Enter feedback for the documents: ')

user_feedback_tokens = word_tokenize(user_feedback_input)
print(user_feedback_tokens)

1   రామ్ పోతినేని
2   రామ్ చరణ్ తేజా
12   రామ్ చరణ్ తేజా
29   నందమురి కళ్యాణ్ రామ్
Enter feedback for the documents: 2 12
['2', '12']


In [64]:
dictionary = {}
dictionary[user_string] = user_feedback_tokens
dictionary

{'రామ్ చరణ్ తేజా': ['2', '12']}

In [65]:
user_query = input('Give any Director of a movie... we recommend movies for you...')
isThere = False

if user_query in dictionary:
    isThere = True
    for doc_id in dictionary[user_query]:
        if doc_id in all_doc_id:
            all_doc_id.remove(doc_id)
            
else:
    user_tokens = word_tokenize(user_query)
    user_tokens
    final_user_tokens = []

    for token in user_tokens:
        final_user_tokens.append(token.lower())

    user_dict = {}
    docId_list = []

    def print_inverted(iwd):
        index = 0
        for key in iwd:
            print(key,end=' ')
            cnode = iwd[key][0]
            while cnode != None:
    #             print(cnode.docId, end=' ')
                docId_list.insert(index, cnode.docId)
                index += 1
                cnode = cnode.next

            print(' ')


    for i,word in enumerate(final_user_tokens):
        if word in iwd:
            user_dict[word] = iwd[word]

    print_inverted(user_dict)
    print(' ')
    docId_set = set(docId_list)
    # print('docId_set:','\n',  docId_set)
    # print(' ')
    print('docId_set is of length', len(docId_list))
    print(' ')
    print('Movies based on your search:')
    print(' ')
    count = 0
    retrieved_movies = []
    if len(docId_set) == 0:
        print('No movies based on your given Director...')
    else:
        for item in docId_set:
            if item in telugu_movies1['id']:
                print(telugu_movies1.loc[item])
#                 retrieved_movies.insert(count,telugu_movies1.loc[item])
                count += 1
                print(' ')

    print('Total no.of movies:', count)
    
    
if isThere:
    for item in dictionary[user_query]:
        print(telugu_movies.iloc[int(item)])
        
    for item in all_doc_id:
        print(telugu_movies.iloc[int(item)])

Give any Director of a movie... we recommend movies for you...రామ్ చరణ్ తేజా
Name                                                    రంగస్థలం
Genres                                            యాక్షన్ డ్రామా
Actors                                            రామ్ చరణ్ తేజా
Directors                                               సుకుమార్
Description    చిట్టి బాబు తన అన్నయ్య జీవితానికి వారి గ్రామ అ...
Keywords                                                     8.2
Name: 2, dtype: object
Name                                                      మగధీరా
Genres                                     యాక్షన్ డ్రామా ఫాంటసీ
Actors                                            రామ్ చరణ్ తేజా
Directors                                           S.S. రాజమౌలి
Description    400 సంవత్సరాల తరువాత ఒక యోధుడు పునర్జన్మ పొందు...
Keywords                                                     7.7
Name: 12, dtype: object
Name                                               ఆ పోరాటయోధుడు
Genres                         